## Overview
We will tune and pilot with the 500 most frequent monosyllabic words from TASA.

In [1]:
# python: base (3.11.4)

import numpy as np
import json
import pandas as pd
import time
import tensorflow as tf
from tensorflow.keras.optimizers import Adam

from tensorflow.keras import backend as K


from src.learner import *
from utilities import *


# data
kidwords = pd.read_csv('data/kidwords/kidwords.csv', header=None)[0].tolist()

top_500 = pd.read_csv('data/top_500.csv')
bottom_500 = pd.read_csv('data/infrequent_500.csv')
train_word_indices = np.array([i for i, e in enumerate(kidwords) if e in top_500['word'].values])
control_word_indices = np.array([i for i, e in enumerate(kidwords) if e in bottom_500['word'].values])

XX = np.genfromtxt('data/kidwords/orth.csv', delimiter=",")
YY = np.genfromtxt('data/kidwords/phon.csv', delimiter=",")

non_zero_a = np.any(XX != 0, axis=0)
X = XX[:, non_zero_a]

non_zero_b = np.any(YY != 0, axis=0)
Y = YY[:, non_zero_b]

# configs
with open('data/config.json', "r") as f:
    cfg = json.load(f)


2024-08-12 11:44:17.879233: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-08-12 11:44:17.897601: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-08-12 11:44:17.922330: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-08-12 11:44:17.927335: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-08-12 11:44:17.944321: I tensorflow/core/platform/cpu_feature_guar

GPU check

In [2]:
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))

Num GPUs Available:  1


I0000 00:00:1723477460.710287 1500331 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
I0000 00:00:1723477460.758643 1500331 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
I0000 00:00:1723477460.759977 1500331 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355


In [4]:
def calculate_error(model, X, Y):
    predictions = model.predict(X)
    mse = np.mean((predictions - Y) ** 2, axis=1)
    return mse

def sample_N_to_quartiles_min(x, N, y):

    """Calculate quartiles and min. Return the one you want.

    Returns
    -------
    array : an array of N indices for values that represent the kind specified in y.

    """
    quartiles = np.percentile(x, [25, 50, 75])
    minimum = np.min(x)
    maximum = np.max(x)
    
    # Function to find the closest N indices for values to a given value
    def closest_values(arr, value, N):
        indices = np.argsort(np.abs(arr - value))[:N]
        return indices
        # if you want the values for error instead of the indices:
        return arr[indices]

    if y == "q1":
        return closest_values(x, quartiles[0], N)
    if y == "q2":
        return closest_values(x, quartiles[1], N)
    if y == "q3":
        return closest_values(x, quartiles[2], N)
    if y == "min":
        return closest_values(x, minimum, N)
    if y == "max":
        return closest_values(x, maximum, N)


In [5]:
frequencies = {}

for word in top_500['word']:
    rowmatch = top_500[top_500['word']==word]
    if not rowmatch.empty:
        frequencies[word] = rowmatch['frequency'].values[0]+1
    # all frequencies should be present, but just in case...
    else:
        frequencies[word] = 1


In [6]:
def scale_frequencies(frequencies):
    """
    Scales the given word frequencies between 0 and 1.
    
    Parameters:
    frequencies (dict): A dictionary where keys are words and values are their frequencies.
    
    Returns:
    dict: A dictionary with scaled frequencies.
    """
    max_freq = max(frequencies.values())
    scaled_frequencies = {word: freq / max_freq for word, freq in frequencies.items()}
    return scaled_frequencies

In [7]:
scaled_frequencies = scale_frequencies(frequencies)
frequency_weights = np.array([scaled_frequencies[word] for word in top_500['word']])

## Representational domain #1: top 500 most frequent words
### Condition 1: maximum on distribution of MSE (i.e., the hardest condition)
The first condition is the most difficult: the 20 closest words to the maximum of the distribution for MSE are selected as the "zone" and presented at each epoch.

Note: Each routine with 20 samples at 500 epochs takes about an hour or so.

In [8]:
# Training loop

samples = 20
epochs = 500

with open('outputs/max_values_mse_samples.csv', 'w') as f:

    # write column names
    f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                            "seed",
                            "epoch",
                            "loss_train",
                            "accuracy_train",
                            "mse_train",
                            "loss_remaining_train_pool",
                            "accuracy_remaining_train_pool",
                            "mse_remaining_train_pool",
                            "loss_test",
                            "accuracy_test",
                            "mse_test"))

    for sample in range(samples):

        seed = cfg['seed'] + sample
        model = learner(X, Y, seed=seed, hidden=cfg['hidden_units'], optimizer=Adam(learning_rate=cfg['learning_rate']))

        for epoch in range(epochs):
            
            mse = calculate_error(model, X[train_word_indices], Y[train_word_indices])
            selected_indices = sample_N_to_quartiles_min(mse, cfg['N'], "max")
                
            zpd = [e for i, e in enumerate(train_word_indices) if i in selected_indices]
            remaining_pool = [e for i, e in enumerate(train_word_indices) if i not in selected_indices]

            # Find indices of the 20 items around the identified zone based on MSE
            
            x = X[selected_indices]
            y = Y[selected_indices]
            
            # Train the model on the selected items
            model.fit(X[zpd], Y[zpd], epochs=1, verbose=1)

            loss_train, accuracy_train, mse_train = model.evaluate(X[zpd], Y[zpd], verbose=0) 
            loss_remaining_train_pool, accuracy_remaining_train_pool, mse_remaining_train_pool = model.evaluate(X[remaining_pool], Y[remaining_pool], verbose=0) 
            loss_test, accuracy_test, mse_test = model.evaluate(X[~train_word_indices], Y[~train_word_indices], verbose=0) 

            f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                                            seed,
                                            epoch,
                                            loss_train,
                                            accuracy_train,
                                            mse_train,
                                            loss_remaining_train_pool,
                                            accuracy_remaining_train_pool,
                                            mse_remaining_train_pool,
                                            loss_test,
                                            accuracy_test,
                                            mse_test))


I0000 00:00:1723477479.479806 1500331 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
I0000 00:00:1723477479.480157 1500331 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
I0000 00:00:1723477479.480532 1500331 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
I0000 00:00:1723477479.595403 1500331 cuda_executor.cc:1015] successful NUMA node read from SysFS ha

 1/16 ━━━━━━━━━━━━━━━━━━━━ 8s 599ms/step

I0000 00:00:1723477480.421616 1500579 device_compiler.h:188] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


16/16 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - binary_accuracy: 0.4023 - loss: 0.7277 - mse: 0.2670
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step - binary_accuracy: 0.4266 - loss: 0.7154 - mse: 0.2610
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - binary_accuracy: 0.4625 - loss: 0.7065 - mse: 0.2566
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step - binary_accuracy: 0.4945 - loss: 0.6990 - mse: 0.2529
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step - binary_accuracy: 0.5320 - loss: 0.6925 - mse: 0.2497
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step - binary_accuracy: 0.5539 - loss: 0.6865 - mse: 0.2467
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step - binary_accuracy: 0.5914 - loss: 0.6804 - mse: 0.2436
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32m

### Condition #2: 75th percentile based on MSE
This is the second most difficult condition. At each epoch the 20 words that are closest to the 75th percentile on MSE are selected for learning. All other hyperparameters are held constant. This percentile is also labeled as the 3rd quartile (Q3) in the code.

In [9]:
# Training loop

samples = 20
epochs = 500

with open('outputs/75th_percentile_values_mse_samples.csv', 'w') as f:

    # write column names
    f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                            "seed",
                            "epoch",
                            "loss_train",
                            "accuracy_train",
                            "mse_train",
                            "loss_remaining_train_pool",
                            "accuracy_remaining_train_pool",
                            "mse_remaining_train_pool",
                            "loss_test",
                            "accuracy_test",
                            "mse_test"))

    for sample in range(samples):

        seed = cfg['seed'] + sample
        model = learner(X, Y, seed=seed, hidden=cfg['hidden_units'], optimizer=Adam(learning_rate=cfg['learning_rate']))

        for epoch in range(epochs):
            
            mse = calculate_error(model, X[train_word_indices], Y[train_word_indices])
            selected_indices = sample_N_to_quartiles_min(mse, cfg['N'], "q3")
                
            zpd = [e for i, e in enumerate(train_word_indices) if i in selected_indices]
            remaining_pool = [e for i, e in enumerate(train_word_indices) if i not in selected_indices]

            # Find indices of the 20 items around the identified zone based on MSE
            
            x = X[selected_indices]
            y = Y[selected_indices]
            
            # Train the model on the selected items
            model.fit(X[zpd], Y[zpd], epochs=1, verbose=1)

            loss_train, accuracy_train, mse_train = model.evaluate(X[zpd], Y[zpd], verbose=0) 
            loss_remaining_train_pool, accuracy_remaining_train_pool, mse_remaining_train_pool = model.evaluate(X[remaining_pool], Y[remaining_pool], verbose=0) 
            loss_test, accuracy_test, mse_test = model.evaluate(X[~train_word_indices], Y[~train_word_indices], verbose=0) 

            f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                                            seed,
                                            epoch,
                                            loss_train,
                                            accuracy_train,
                                            mse_train,
                                            loss_remaining_train_pool,
                                            accuracy_remaining_train_pool,
                                            mse_remaining_train_pool,
                                            loss_test,
                                            accuracy_test,
                                            mse_test))

16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 755ms/step - binary_accuracy: 0.4695 - loss: 0.7064 - mse: 0.2565
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 759us/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - binary_accuracy: 0.5016 - loss: 0.6973 - mse: 0.2520
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step - binary_accuracy: 0.5312 - loss: 0.6890 - mse: 0.2479
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 997us/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step - binary_accuracy: 0.5727 - loss: 0.6810 - mse: 0.2440
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 792us/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - binary_accuracy: 0.6070 - loss: 0.6732 - mse: 0.2401
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step - binary_accuracy: 0.6313 - loss: 0.6654 - mse: 0.2362
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 711us/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - binary_accuracy: 0.6586 - loss: 0.6562 - mse: 0.2317
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 791us/step
1/1 ━━━━━━━━━━━━━━━━━━━━

### Condition #3: 50th percentile on distribution of MSE
Here we select the 20 nearest words from the 50th percentile in mean squared error. These are the 2nd quartile (Q2 in the code).

In [10]:
# Training loop

samples = 20
epochs = 500

with open('outputs/50th_percentile_values_mse_samples.csv', 'w') as f:

    # write column names
    f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                            "seed",
                            "epoch",
                            "loss_train",
                            "accuracy_train",
                            "mse_train",
                            "loss_remaining_train_pool",
                            "accuracy_remaining_train_pool",
                            "mse_remaining_train_pool",
                            "loss_test",
                            "accuracy_test",
                            "mse_test"))

    for sample in range(samples):

        seed = cfg['seed'] + sample
        model = learner(X, Y, seed=seed, hidden=cfg['hidden_units'], optimizer=Adam(learning_rate=cfg['learning_rate']))

        for epoch in range(epochs):
            
            mse = calculate_error(model, X[train_word_indices], Y[train_word_indices])
            selected_indices = sample_N_to_quartiles_min(mse, cfg['N'], "q2")
                
            zpd = [e for i, e in enumerate(train_word_indices) if i in selected_indices]
            remaining_pool = [e for i, e in enumerate(train_word_indices) if i not in selected_indices]

            # Find indices of the 20 items around the identified zone based on MSE
            
            x = X[selected_indices]
            y = Y[selected_indices]
            
            # Train the model on the selected items
            model.fit(X[zpd], Y[zpd], epochs=1, verbose=1)

            loss_train, accuracy_train, mse_train = model.evaluate(X[zpd], Y[zpd], verbose=0) 
            loss_remaining_train_pool, accuracy_remaining_train_pool, mse_remaining_train_pool = model.evaluate(X[remaining_pool], Y[remaining_pool], verbose=0) 
            loss_test, accuracy_test, mse_test = model.evaluate(X[~train_word_indices], Y[~train_word_indices], verbose=0) 

            f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                                            seed,
                                            epoch,
                                            loss_train,
                                            accuracy_train,
                                            mse_train,
                                            loss_remaining_train_pool,
                                            accuracy_remaining_train_pool,
                                            mse_remaining_train_pool,
                                            loss_test,
                                            accuracy_test,
                                            mse_test))

16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - binary_accuracy: 0.5070 - loss: 0.6974 - mse: 0.2521
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - binary_accuracy: 0.5312 - loss: 0.6876 - mse: 0.2473
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step - binary_accuracy: 0.5984 - loss: 0.6790 - mse: 0.2430
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - binary_accuracy: 0.6086 - loss: 0.6700 - mse: 0.2385
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - binary_accuracy: 0.6586 - loss: 0.6599 - mse: 0.2336
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - binary_accuracy: 0.6813 - loss: 0.6496 - mse: 0.2285
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - binary_accuracy: 0.7172 - loss: 0.6381 - mse: 0.2228
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33m

### Condition #4: The 25th percentile in MSE
This condition samples the 20 words that are closest to the 25th percentile in mean squared error (1st quartile/ Q1).

In [11]:
# Training loop

samples = 20
epochs = 500

with open('outputs/25th_percentile_values_mse_samples.csv', 'w') as f:

    # write column names
    f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                            "seed",
                            "epoch",
                            "loss_train",
                            "accuracy_train",
                            "mse_train",
                            "loss_remaining_train_pool",
                            "accuracy_remaining_train_pool",
                            "mse_remaining_train_pool",
                            "loss_test",
                            "accuracy_test",
                            "mse_test"))

    for sample in range(samples):

        seed = cfg['seed'] + sample
        model = learner(X, Y, seed=seed, hidden=cfg['hidden_units'], optimizer=Adam(learning_rate=cfg['learning_rate']))

        for epoch in range(epochs):
            
            mse = calculate_error(model, X[train_word_indices], Y[train_word_indices])
            selected_indices = sample_N_to_quartiles_min(mse, cfg['N'], "q1")
                
            zpd = [e for i, e in enumerate(train_word_indices) if i in selected_indices]
            remaining_pool = [e for i, e in enumerate(train_word_indices) if i not in selected_indices]

            # Find indices of the 20 items around the identified zone based on MSE
            
            x = X[selected_indices]
            y = Y[selected_indices]
            
            # Train the model on the selected items
            model.fit(X[zpd], Y[zpd], epochs=1, verbose=1)

            loss_train, accuracy_train, mse_train = model.evaluate(X[zpd], Y[zpd], verbose=0) 
            loss_remaining_train_pool, accuracy_remaining_train_pool, mse_remaining_train_pool = model.evaluate(X[remaining_pool], Y[remaining_pool], verbose=0) 
            loss_test, accuracy_test, mse_test = model.evaluate(X[~train_word_indices], Y[~train_word_indices], verbose=0) 

            f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                                            seed,
                                            epoch,
                                            loss_train,
                                            accuracy_train,
                                            mse_train,
                                            loss_remaining_train_pool,
                                            accuracy_remaining_train_pool,
                                            mse_remaining_train_pool,
                                            loss_test,
                                            accuracy_test,
                                            mse_test))

16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - binary_accuracy: 0.5312 - loss: 0.6883 - mse: 0.2476
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step - binary_accuracy: 0.5758 - loss: 0.6801 - mse: 0.2435
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step - binary_accuracy: 0.6273 - loss: 0.6718 - mse: 0.2394
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - binary_accuracy: 0.6555 - loss: 0.6628 - mse: 0.2349
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step - binary_accuracy: 0.6906 - loss: 0.6525 - mse: 0.2298
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step - binary_accuracy: 0.7359 - loss: 0.6417 - mse: 0.2245
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - binary_accuracy: 0.7508 - loss: 0.6291 - mse: 0.2184
16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms

KeyboardInterrupt: 

### Condition #5: The minimum values on mean squared error (i.e., the easiest condition)
This last condition of the set selects the 20 words that are at minimum for mean squared error. This is the easiest condition.

In [ ]:
# Training loop

samples = 20
epochs = 500

with open('outputs/min_values_mse_samples.csv', 'w') as f:

    # write column names
    f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                            "seed",
                            "epoch",
                            "loss_train",
                            "accuracy_train",
                            "mse_train",
                            "loss_remaining_train_pool",
                            "accuracy_remaining_train_pool",
                            "mse_remaining_train_pool",
                            "loss_test",
                            "accuracy_test",
                            "mse_test"))

    for sample in range(samples):

        seed = cfg['seed'] + sample
        model = learner(X, Y, seed=seed, hidden=cfg['hidden_units'], optimizer=Adam(learning_rate=cfg['learning_rate']))

        for epoch in range(epochs):
            
            mse = calculate_error(model, X[train_word_indices], Y[train_word_indices])
            selected_indices = sample_N_to_quartiles_min(mse, cfg['N'], "min")
                
            zpd = [e for i, e in enumerate(train_word_indices) if i in selected_indices]
            remaining_pool = [e for i, e in enumerate(train_word_indices) if i not in selected_indices]

            # Find indices of the 20 items around the identified zone based on MSE
            
            x = X[selected_indices]
            y = Y[selected_indices]
            
            # Train the model on the selected items
            model.fit(X[zpd], Y[zpd], epochs=1, verbose=1)

            loss_train, accuracy_train, mse_train = model.evaluate(X[zpd], Y[zpd], verbose=0) 
            loss_remaining_train_pool, accuracy_remaining_train_pool, mse_remaining_train_pool = model.evaluate(X[remaining_pool], Y[remaining_pool], verbose=0) 
            loss_test, accuracy_test, mse_test = model.evaluate(X[~train_word_indices], Y[~train_word_indices], verbose=0) 

            f.write("{},{},{},{},{},{},{},{},{},{},{}\n".format(
                                            seed,
                                            epoch,
                                            loss_train,
                                            accuracy_train,
                                            mse_train,
                                            loss_remaining_train_pool,
                                            accuracy_remaining_train_pool,
                                            mse_remaining_train_pool,
                                            loss_test,
                                            accuracy_test,
                                            mse_test))